### Pyart_gridplot_panels.py
Author: djv 7/19
This script will compare Raw level II reflectivity to gridded radar output 
created from  *pyart.map.grid_from_radars.py*. <br> Will plot out maps of raw data at given
sweep and gridded data at level closest to sweep elevation as well as cross sections of the gridded datatest using **PYART** routines:
    1. *plot_latitude_slice*
    2. *plot_longitude_slice* 
    3. *plot_ppi_map*
    4. *plot_grid*
    
**This script has several plotting sections:**
    1. 4-panel plot of radars+cross sections
    2. Widget plots:
    *- 2-panel plot of map of gridded radar with longitudinal cross section with adjustable slider widget
    *- 2-panel plot of map of gridded radar with latitudinal cross section with adjustable slider widget
    *- 2-panel plot of latitudinal and longitudinal cross section with adjustable slider widgets
    
Program Needs several user input files:
    A Level II radar archive file
    A gridded version of this data created from pyart.map.grid_from_radars.py
    
    Will also run python script args_gridplt.py to read in input data params

In [ ]:
import pyart
import math
import numpy as np
import cartopy
import matplotlib.gridspec as gridspec
import matplotlib.pyplot as plt
import matplotlib.colors as col
import matplotlib.cm as cm
from ipywidgets import interactive
import ipywidgets as widgets
from IPython.display import display as wdisplay
from IPython.html.widgets import *
import sys
sys.path.insert(0, '/home/djv/python/djvlibs/')   #DEFINES DJV LIB PATH
from dvpylib_shape import *
%matplotlib inline

### Run interactive parameter program 
edit following line to reflect desired sweep plotting parameter and plot output
plttyp=png,ps,eps,jpg,screen

In [ ]:
###################   MAIN PROGRAM ##################################%
%run /home/djv/python/notebooks/radar/args_gridplt.py 1 3000 reflectivity png
#name = raw_input("What's your name? ")   #inputs as strings
print(sweep,type(sweep))
print(grd_elev,type(grd_elev))
print(pltvar,type(pltvar))

In [ ]:
#############  USER DEF VARIABLES #################
radmax=250.                  #radius of Lev II plot map area
grid_line_delta = 1.0
xsec_vlim = [0,15]           #vertical limit of xsec plots(km)
xsec_hlim = [-200.,200.]     #horizontal limit of xsec plot(km)
nexrad_site="KCRP"
xdate="20170826_002504"

datpth = "/jm11/djv/radar/pyart/"
ifile=datpth+nexrad_site+xdate+"_V06.ar2v"
ifile=datpth+nexrad_site+"20170826_0025_velocityallsw.nc"  #dealiased velocity
gfile=datpth+"KCRP201708260025_all_250km_grid_41x501_dist.nc"

ofile0 = nexrad_site+xdate+pltvar+"grdtst_4pan"   #plot output name

In [ ]:
def map_add_on(ax,map_res,lonvals,latvals):
    import matplotlib.ticker as mticker
    import cartopy.feature as cfeature
    from metpy.plots import USCOUNTIES
################# CARTOPY ADD_ONS  ######################
    ax.add_feature(USCOUNTIES.with_scale('20m'), linewidth=1,linestyle='--',edgecolor='darkgray')
    ax.add_feature(cfeature.LAND)
    ax.add_feature(cfeature.OCEAN)
    ax.add_feature(cfeature.LAKES.with_scale(map_res), alpha=0.5)
    ax.add_feature(cfeature.RIVERS.with_scale(map_res), edgecolor='tab:blue') 


In [ ]:
def find_nearest(array, value):
# Will return index of array_val closest to value
# Return: index of nearest value
    array = np.asarray(array)
    idx = (np.abs(array - value)).argmin()
    return idx

# Main Program Starts Here#

In [ ]:
############## Creates REF colormap ###############
#'pyart_NWSRef',
v0=-40
v1=75
cb_pth="/home11/staff/djv/python/"
cfil=cb_pth+"djv_radar_bin5.rgb"
if pltvar != "reflectivity":
    cfil=cb_pth+"djv_vad_bin5.rgb"
    v0=-65.
    v1=65.
chan="RADAR"
dvrad,ncolor=dvColormap(cfil,chan,"")  #RGB colorfile,channel,path
dv_cmap=col.LinearSegmentedColormap('my_colormap',dvrad,N=ncolor,gamma=1.)


In [ ]:
################## GRIDDED SECTION #######################
rg = pyart.io.read_grid(gfile)
rg.fields.keys()
displayg = pyart.graph.GridMapDisplay(rg)
clatg=rg.origin_latitude['data'][0]
clong=rg.origin_longitude['data'][0]
xs_lon=clong+0.9             #location of lat(NS) xsec wrt radar
xs_lat=clatg+.1                 #location of lon(WE) xsec
xvals=rg.x['data'][:]
grd_res=str((int((xvals[-1]-xvals[0])/(len(xvals)-1))/1000))+"km"  #determines horiz res
glev =find_nearest(rg.z['data'][:],grd_elev)  #find index of desired plot elev

In [ ]:
########### READ AND PLOT PREP of LEVEL II ARCHIVE DATA ##########
r = pyart.io.read(ifile)
r.fields.keys()
display = pyart.graph.RadarMapDisplay(r)  #set up for map plot
clat=r.latitude['data'][0]
clon=r.longitude['data'][0]
lalo_dphi=(1.1*radmax)/111.11
wlon=clon-lalo_dphi
elon=clon+lalo_dphi
blat=clat-lalo_dphi
ulat=clat+lalo_dphi
lab_dphi=int(abs(wlon-elon)/3.)
lonvals=np.around(np.arange(wlon,elon+lab_dphi,lab_dphi),1)
latvals=np.around(np.arange(blat,ulat+lab_dphi,lab_dphi),1)
sdate=r.time['units'].split()
plt_title=nexrad_site+" "+pltvar+" swp="+str(sweep)+" "+sdate[2]
map_res = '50m'     #map resolution of cartopy features
projection = cartopy.crs.PlateCarree()

## 4-panel Plot 

In [ ]:
# Will compare actual radar map to gridded map at level closest to sweep 
# elevation and plot 2 vertical cross sections
map_panel_axes0 =  [-0.05, 0.52, .43, .43]  # sets up panels for plotting 
map_panel_axes1 =  [0.5, 0.54, .39, .39]
x_cut_panel_axes = [0.05, 0.06, .39 ,.38]
y_cut_panel_axes = [0.55, 0.06, .39, .38]
clat=r.latitude['data'][0]
clon=r.longitude['data'][0]
fig = plt.figure(figsize=[15,7])
########### PLOT LEV II RADAR ON MAP ####################
plt_title=nexrad_site+" "+pltvar+" swp="+str(sweep)+" "+sdate[2]
ax0 = fig.add_axes(map_panel_axes0, projection=projection)
display.plot_ppi_map(pltvar,sweep, vmin=v0, vmax=v1,
         min_lon=wlon, max_lon=elon, min_lat=blat, max_lat=ulat,
         lon_lines=np.arange(int(wlon)-1.0,int(elon)+1.0,grid_line_delta), 
         lat_lines=np.arange(int(blat)-1.0,math.floor(ulat)+2.,grid_line_delta), 
         projection=projection,cmap=dv_cmap,resolution=map_res,colorbar_label="m/s",
         lat_0=clat,lon_0=clon,title=plt_title)
map_add_on(ax0,map_res,lonvals,latvals)
display.plot_range_rings([50, 100])   #plots rings 
ax0.scatter(clon,clat,color='darkblue',edgecolor='k',linewidth='1',s=30,zorder=500)

########### PLOT GRIDDED RADAR ON MAP ####################
ax1 = fig.add_axes(map_panel_axes1, projection=projection)
plt_gtitle=(nexrad_site+" "+grd_res+" grd "+
            pltvar+" lev="+str( rg.z['data'][glev]/1000.)+"kkm \n"+sdate[2])
displayg.plot_grid(pltvar, glev, vmin=v0, vmax=v1,projection=projection,
         cmap=dv_cmap,title=plt_gtitle,ax=ax1,colorbar_label="m/s",axislabels=(' ',' '),
                   axislabels_flag=True)
map_add_on(ax1,map_res,lonvals,latvals)
### Plots station location ####
ax1.scatter(clon,clat,color='darkblue',edgecolor='k',linewidth='1',s=30,zorder=500)
displayg.plot_crosshairs(lon=xs_lon, lat=xs_lat,linestyle='--', color='k')

################## PLOT VERTICAL  CROSS SECTIONS #############
#### longitude slice ####
title="Latitude slice"
ax2 = fig.add_axes(x_cut_panel_axes)
ax2.set_ylim(xsec_vlim)  ### Set vert/horiz ranges of XSEC
ax2.set_xlim(xsec_hlim)
displayg.plot_longitude_slice(pltvar,lon=xs_lon,vmin=v0,vmax=v1,cmap=dv_cmap,
                              colorbar_label="m/s",title=title)
                             
#### latitude slice ####
title="Longitude slice"                                
ax3 = fig.add_axes(y_cut_panel_axes)
ax3.set_ylim(xsec_vlim)  ### Set vert/horiz ranges of XSEC
ax3.set_xlim(xsec_hlim)
displayg.plot_latitude_slice(pltvar,lat=xs_lat,vmin=v0,vmax=v1,cmap=dv_cmap,
                             colorbar_label="m/s",title=title)
#%%%%%%%%%

## Save output plot if desired

In [ ]:
if  plttyp != "screen" and plttyp != "Screen":
    ofile=ofile0+"."+plttyp
    print("Saving as... "+ofile)
    fig.savefig(ofile,format=plttyp,orientation='portrait',quality=100)

## Plot Gridded Map and Interactive choice of Cross section Lats

In [ ]:

def xhair(lt,ln,var,glev,vmin,vmax,proj,cmap,tit,mres,lonvals,latvals,wl,bl):
# Routine to plot grided radar map and longitudingal cross setions
# Uses python slider to move latitudinally to see cross secction evolution
    gs = gridspec.GridSpec(1, 1)
    gs.update(left=0.0, right=0.45, wspace=0.005)
    ax1 = plt.subplot(gs[0],projection=projection)#121)  
    ax1.clear()
    displayg.plot_grid(var, glev, vmin=vmin, vmax=vmax,projection=proj,
                       cmap=cmap,title=tit,ax=ax1,colorbar_flag=False)
    map_add_on(ax1,mres,lonvals,latvals)
    ax1.scatter(clong,clatg,color='darkblue',edgecolor='k',linewidth='1',s=30,zorder=500)
    displayg.plot_crosshairs(lon=ln,lat=lt,linestyle='--', color='k')
    
#  Plot Cross section
    xsec_vlim = [0,15]
    xsec_hlim = [-150.,150.]
    gs1 = gridspec.GridSpec(1, 1)
    gs1.update(left=0.53 ,right=1.,bottom=0.3,top=0.7, wspace=0.005)
    ax2 = plt.subplot(gs1[0])
    ax2.clear()
    title="Longitude slice"
    displayg.plot_latitude_slice(var,lat=lt,vmin=vmin,vmax=vmax,cmap=cmap,
                                 colorbar_label="m/s",title=title)

plt_gtitle=(nexrad_site+" "+grd_res+" grd "+
            pltvar+" lev="+str( rg.z['data'][glev]/1000.)+"km \n"+sdate[2])
interact(xhair,lt=(blat,ulat,0.2),ln=fixed(xs_lon),var=fixed(pltvar),glev=fixed(glev),
         vmin=fixed(v0),vmax=fixed(v1),proj=fixed(projection),cmap=fixed(dv_cmap),
         tit=fixed(plt_gtitle),mres=fixed(map_res),lonvals=fixed(lonvals),
         latvals=fixed(latvals),wl=fixed(wlon),bl=fixed(blat))
#%%%%%%%%%%%%%%%%

## Plot Gridded Map and Interactive choice of Cross section Lons

In [ ]:
def yhair(lt,ln,var,glev,vmin,vmax,proj,cmap,tit,mres,lonvals,latvals,wl,bl):
# Routine to plot grided radar map and latitudingal cross setions
# Uses python slider to move longitudinally to see cross secction evolution
    gs = gridspec.GridSpec(1, 1)
    gs.update(left=0.0, right=0.45, wspace=0.005)
    ax1 = plt.subplot(gs[0],projection=projection)#121)  
    ax1.clear()
    displayg.plot_grid(var, glev, vmin=vmin, vmax=vmax,projection=proj,
                       cmap=cmap,title=tit,ax=ax1,colorbar_flag=False)
    map_add_on(ax1,mres,lonvals,latvals)
    ax1.scatter(clong,clatg,color='darkblue',edgecolor='k',linewidth='1',s=30,zorder=500)
    displayg.plot_crosshairs(lon=ln,lat=lt,linestyle='--', color='k')
    
#  Plot Cross section
    xsec_vlim = [0,15]
    xsec_hlim = [-150.,150.]
    gs1 = gridspec.GridSpec(1, 1)
    gs1.update(left=0.53 ,right=1.,bottom=0.3,top=0.7, wspace=0.005)
    ax2 = plt.subplot(gs1[0])
    ax2.clear()
    title="Latitude slice"
    displayg.plot_longitude_slice(var,lon=ln,vmin=vmin,vmax=vmax,cmap=cmap,
                                 colorbar_label="m/s",title=title)

plt_gtitle=(nexrad_site+" "+grd_res+" grd "+
            pltvar+" lev="+str( rg.z['data'][glev]/1000.)+"km \n"+sdate[2])
interact(yhair,lt=fixed(xs_lat),ln=(wlon,elon,0.2),var=fixed(pltvar),glev=fixed(glev),
         vmin=fixed(v0),vmax=fixed(v1),proj=fixed(projection),cmap=fixed(dv_cmap),
         tit=fixed(plt_gtitle),mres=fixed(map_res),lonvals=fixed(lonvals),
         latvals=fixed(latvals),wl=fixed(wlon),bl=fixed(blat))
#%%%%%%%%%%%%%%%%

## Plot Interactive choice of Cross sections Lats+ Lons

In [ ]:
########### PLOT VERTICAL CROSS SECTIONS ################
def latxsec(ln,var,vmin,vmax,cmap):
    displayg.plot_longitude_slice(var,lon=ln,vmin=vmin,vmax=vmax,cmap=cmap,
                                  colorbar_label="m/s",title=title)

def lonxsec(lt,var,vmin,vmax,cmap):
    displayg.plot_latitude_slice(var,lat=lt,vmin=vmin,vmax=vmax,cmap=cmap,
                                  colorbar_label="m/s",title=title)

#### latitude slice ####
x_cut_panel_axes = [0.05, 0.30, .4, .25]
ax2 = fig.add_axes(x_cut_panel_axes)
ax2.set_ylim(xsec_vlim)  ### Set vert/horiz ranges of XSEC
ax2.set_xlim(xsec_hlim)
title="Latitude Slice"
interact(latxsec,ln=(wlon,elon,0.2),var=fixed(pltvar),vmin=fixed(v0),vmax=fixed(v1),
         cmap=fixed(dv_cmap))

#### longitude slice ####
y_cut_panel_axes = [0.55, 0.30, .4, .25]
ax3 = fig.add_axes(y_cut_panel_axes)
ax3.set_ylim(xsec_vlim)  ### Set vert/horiz ranges of XSEC
ax3.set_xlim(xsec_hlim)
title="Longitude Slice"
interact(lonxsec,lt=(blat,ulat,0.2),var=fixed(pltvar),vmin=fixed(v0),vmax=fixed(v1),
         cmap=fixed(dv_cmap))
#%%%%%%%%%%%

In [ ]:
# Will compare actual radat map to gridded map at level closest to sweep 
# elevation
map_panel_axes0 =  [0.02, 0.03, .5, .5]  # sets up panels for plotting 
map_panel_axes1 =  [0.5, 0.03, .5, .50]

plt_title=nexrad_site+" "+pltvar+" swp="+str(sweep)+" "+sdate[2]
fig = plt.figure(figsize=[15,7])
ax0 = fig.add_axes(map_panel_axes0, projection=projection)
display.plot_ppi_map(pltvar,sweep, vmin=v0, vmax=v1,
         min_lon=wlon, max_lon=elon, min_lat=blat, max_lat=ulat,
         lon_lines=np.arange(int(wlon)-1.0,int(elon)+1.0,grid_line_delta), 
         lat_lines=np.arange(int(blat)-1.0,math.floor(ulat)+2.,grid_line_delta), 
         projection=projection,cmap=dv_cmap,resolution=map_res,colorbar_label="m/s",
         lat_0=clat,lon_0=clon,title=plt_title)
map_add_on(ax0,map_res,lonvals,latvals)
display.plot_range_rings([50, 100])   #plots rings 
ax0.scatter(clon,clat,color='darkblue',edgecolor='k',linewidth='1',s=30,zorder=500)

########### PLOT GRIDDED RADAR ON MAP ####################
ax1 = fig.add_axes(map_panel_axes1, projection=projection)
plt_gtitle=(nexrad_site+" "+grd_res+" grd "+
            pltvar+" lev="+str( rg.z['data'][glev]/1000.)+"kkm \n"+sdate[2])
displayg.plot_grid(pltvar, glev, vmin=v0, vmax=v1,projection=projection,
         cmap=dv_cmap,title=plt_gtitle,ax=ax1,colorbar_label="m/s",axislabels=(' ',' '),
                   axislabels_flag=True)
map_add_on(ax0,map_res,lonvals,latvals)
### Plots station location ####
ax1.scatter(clon,clat,color='darkblue',edgecolor='k',linewidth='1',s=30,zorder=500)
#%%%%%%%%%

##Program End

##Program End